# Did We Really Desegregate?: Predicting School Zones with Demographic Data
## A model to determine how predictive demographic features are of elementary school zones

Charlottesville, Virginia, like every other town in the United States, has a checkered history with race relations and public education. The city school district has sought to remedy historic wrongs by updating its school zones and eliminating maps that were drawn to keep black kids out of historically white schools. This project looks at the current map and investigates the degree to which race still informs assigned school zone. Using census data about race, economic status, education levels, age spread, and details about housing, I was able to build a model that could predict a block's assigned school district with 82.7% accuracy. My model that relied only on racial makeup predicted the correct school only 31.6% of the time, hardly better than a dummy model.
 
![swings](images/aaron-burden-ob6O_xd67O0-unsplash.jpg)
Photo by <a href="https://unsplash.com/@aaronburden?utm_source=unsplash&utm_medium=referral&utm_content=creditCopyText">Aaron Burden</a> on <a href="https://unsplash.com/photos/ob6O_xd67O0?utm_source=unsplash&utm_medium=referral&utm_content=creditCopyText">Unsplash</a>
 
GitHub Repository: https://github.com/LydiaCuffman/cville_school_zones


## Business Understanding and Data Understanding
Charlottesville City Schools integrated under duress. Initially the superintendent closed the schools rather than integrate them. While the schools did eventually reopen and ostensibly integrated, what followed were decades of less overt segregation. <a href="https://www.nytimes.com/2018/10/16/us/charlottesville-riots-black-students-schools.html">The New York Times</a> reported on this history of discrimination against black students in a 2018 article. One illustrative example is Venable Elementary School, the school closest to the University of Virginia and the school cited in the article as having the highest test scores in the division. Students in a predominantly black neighborhood a half mile from the school were zoned for a school three miles away. That racist choice was only fully rectified in 2022, when the school board voted to adjust the school zoning map. The school division also issued an apology to community members for <a href="https://www.cvilletomorrow.org/after-half-a-century-bussing-kids-from-a-historically-black-public-housing-community-away-from-their-neighborhood-school-city-schools-votes-to-rezone-venable/">"historic and recent mistreatment."</a>

This project seeks to determine how equitable the new zoning map is. Now that an obviously racially motivated choice has been fixed, to what degree does the racial makeup of a neighborhood predict the elementary school its students are assigned to?

I used data from opendata.charlottesville.org as well as data collected by the Virginia Equity Center. Both data sets pull from the United States Census, but I found them easier to use than the direct Census Bureau portal. The Census breaks its data down on a variety of scales, with the smallest being Block. I overlaid the Charlottesville City Schools elementary school zone map with the Census blocks to build my data set. My racial data was at the Block level and my other demographic details were at the Block Group (one level up) level. My non-racial demographic data was largely focused on economic status, including features like median household income, percentage of population with health insurance, households receiving public health insurance and/or SNAP benefits, home-ownership rates, and the number of cost-burdened renters. Additionally I included the age breakdown of each Block Group along with details about number of housing units and how many of those units are vacant. 

In [1]:
import pandas as pd
import geopandas as gpd
import folium
import json
import xgboost
from folium.map import Popup, Tooltip
from folium.features import GeoJsonPopup, GeoJsonTooltip
from shapely.geometry import Polygon
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.dummy import DummyClassifier 
from sklearn.linear_model import LogisticRegressionCV
from sklearn.impute import KNNImputer
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.pipeline import Pipeline
from sklearn.tree import DecisionTreeClassifier
from sklearn.decomposition import PCA
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
from sklearn.ensemble import RandomForestClassifier

In [2]:
#Load in a GeoJSON of Charlottesville census blocks
data = gpd.read_file('data/cville_census_blocks.geojson')

In [3]:
#Load in a GeoJSON of the elementary school zone boundaries
schools = gpd.read_file('data/cville_school_zones.geojson')
schools

id  OBJECTID           ZONE  created_user  created_date  last_edited_user  \
0  0         2          Clark           NaN           NaN               NaN   
1  1         4    Jackson-Via           NaN           NaN               NaN   
2  2         5        Johnson           NaN           NaN               NaN   
3  3         6     Greenbrier           NaN           NaN               NaN   
4  4         1  Burnley-Moran           NaN           NaN               NaN   
5  5         3        Venable           NaN           NaN               NaN   

   last_edited_date                                           geometry  
0               NaN  POLYGON ((-78.47802 38.02863, -78.48150 38.029...  
1               NaN  POLYGON ((-78.49029 38.02682, -78.49203 38.027...  
2               NaN  POLYGON ((-78.49289 38.02676, -78.49275 38.026...  
3               NaN  MULTIPOLYGON (((-78.47221 38.06803, -78.47100 ...  
4               NaN  POLYGON ((-78.49375 38.03334, -78.49380 38.033...  
5               NaN  POLYGON ((-78.47841 38.04517, -78.47901 38.045...

In [4]:
schools=schools.drop(columns=['created_user', 'created_date', 'last_edited_user', 'last_edited_date'], axis=1)

In [5]:
#Set variables for each school's boundaries
clark = schools['geometry'][0]
jv = schools['geometry'][1]
johnson = schools['geometry'][2]
greenbrier = schools['geometry'][3]
bm = schools['geometry'][4]
venable = schools['geometry'][5]

In [6]:
#Visualize the six school zones along with the census blocks
m = folium.Map(location=(38.034, -78.477), zoom_start=13)

folium.GeoJson(data,
    style_function=lambda feature: {
        'weight':1,
        "color": "blue",
        'fill_opacity':0
    },
).add_to(m)

popup = GeoJsonPopup(
    fields=['ZONE'],
    aliases=["School"],
    localize=True,
    labels=True,
    style="background-color: yellow;"
)

tooltip = GeoJsonTooltip(
    fields=['ZONE'],
    aliases=["Elementary Zone"],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """,
    max_width=800,
)


folium.GeoJson(schools, style_function = lambda x: {"fillColor": 'red' if x['properties']['ZONE']=="Clark" 
else ('blue' if x['properties']['ZONE']=="Jackson-Via" 
else ('orange' if x['properties']['ZONE']=="Johnson" 
else ('yellow' if x['properties']['ZONE']=="Burnley-Moran"
else ('purple' if x['properties']['ZONE']=="Greenbrier" else 'green')))), "weight": 4, 
                                                                         "color": "black", 'fill_opacity':1, 
                                                                         'fill':True}, popup=popup, tooltip=tooltip).add_to(m)



m

In [7]:
m.save("school_zones.html")

In [21]:
#Write a function that will label each block by its assigned school
def find_school_zone(schools, data):
    for x in range(803):
        if clark.contains(data['geometry'][x])==True:
            data['school_zone'][x]="Clark",
        elif jv.contains(data['geometry'][x])==True:
            data['school_zone'][x]="Jackson-Via",
        elif johnson.contains(data['geometry'][x])==True:
            data['school_zone'][x]="Johnson",
        elif greenbrier.contains(data['geometry'][x])==True:
            data['school_zone'][x]="Greenbrier",
        elif bm.contains(data['geometry'][x])==True:
            data['school_zone'][x]="Burnley-Moran",
        elif venable.contains(data['geometry'][x])==True:
            data['school_zone'][x]="Venable",
        else: data['school_zone'][x]="Manual"

In [22]:
#Make the new column, set a default
data['school_zone']="Manual"

In [23]:
#Run the function
pd.options.mode.chained_assignment = None
find_school_zone(schools, data)

In [24]:
#Check counts
data['school_zone'].value_counts()

Manual              196
(Venable,)          189
(Burnley-Moran,)    175
(Clark,)             78
(Greenbrier,)        66
(Jackson-Via,)       53
(Johnson,)           46
Name: school_zone, dtype: int64

In [ ]:
#The function missed about 25% of zones, largely those on borders. Since the data set is rather small, I will
#refer to the visual map and input these school zones manually. In cases of a block that covers multiple attendance
#areas, I will assign to the school that has the clear majority of the zone. If a clear majority is not obvious,
#I will label it "Split".
manuals = data.loc[data['school_zone']=='Manual']

In [ ]:
manuals

In [ ]:
#Inputs generated by creating an ArcGIS map of the two datasets, accessed through opendata.charlottesville.org
data['school_zone'][0]='Venable'
data['school_zone'][2]='Venable'
data['school_zone'][4]='Venable'
data['school_zone'][5]='Venable'
data['school_zone'][6]='Venable'
data['school_zone'][7]='Venable'
data['school_zone'][8]='Venable'
data['school_zone'][9]='Venable'
data['school_zone'][13]='Venable'
data['school_zone'][17]='Venable'
data['school_zone'][19]='Venable'
data['school_zone'][20]='Venable'
data['school_zone'][21]='Venable'
data['school_zone'][24]='Jackson-Via'
data['school_zone'][27]='Jackson-Via'
data['school_zone'][34]='Johnson'
data['school_zone'][40]='Johnson'
data['school_zone'][42]='Jackson-Via'
data['school_zone'][47]='Split'
data['school_zone'][49]='Jackson-Via'
data['school_zone'][52]='Jackson-Via'
data['school_zone'][60]='Johnson'
data['school_zone'][62]='Jackson-Via'
data['school_zone'][65]='Johnson'
data['school_zone'][68]='Jackson-Via'
data['school_zone'][70]='Jackson-Via'
data['school_zone'][74]='Jackson-Via'
data['school_zone'][77]='Venable'
data['school_zone'][78]='Johnson'
data['school_zone'][79]='Venable'
data['school_zone'][83]='Johnson'
data['school_zone'][84]='Split'
data['school_zone'][87]='Johnson'
data['school_zone'][99]='Venable'
data['school_zone'][108]='Venable'
data['school_zone'][110]='Venable'
data['school_zone'][111]='Venable'
data['school_zone'][113]='Venable'
data['school_zone'][115]='Venable'
data['school_zone'][116]='Venable'
data['school_zone'][117]='Venable'
data['school_zone'][123]='Venable'
data['school_zone'][125]='Venable'
data['school_zone'][126]='Venable'
data['school_zone'][127]='Venable'
data['school_zone'][128]='Split'
data['school_zone'][129]='Greenbrier'
data['school_zone'][130]='Greenbrier'
data['school_zone'][131]='Venable'
data['school_zone'][132]='Venable'
data['school_zone'][133]='Venable'
data['school_zone'][135]='Venable'
data['school_zone'][158]='Jackson-Via'
data['school_zone'][166]='Johnson'
data['school_zone'][169]='Split'
data['school_zone'][174]='Jackson-Via'
data['school_zone'][176]='Clark'
data['school_zone'][177]='Clark'
data['school_zone'][178]='Clark'
data['school_zone'][179]='Jackson-Via'
data['school_zone'][183]='Jackson-Via'
data['school_zone'][193]='Jackson-Via'
data['school_zone'][196]='Split'
data['school_zone'][197]='Johnson'
data['school_zone'][198]='Johnson'
data['school_zone'][199]='Johnson'
data['school_zone'][202]='Johnson'
data['school_zone'][205]='Johnson'
data['school_zone'][206]='Clark'
data['school_zone'][209]='Clark'
data['school_zone'][210]='Jackson-Via'
data['school_zone'][212]='Clark'
data['school_zone'][214]='Clark'
data['school_zone'][225]='Greenbrier'
data['school_zone'][232]='Burnley-Moran'
data['school_zone'][233]='Burnley-Moran'
data['school_zone'][235]='Burnley-Moran'
data['school_zone'][236]='Burnley-Moran'
data['school_zone'][238]='Burnley-Moran'
data['school_zone'][239]='Burnley-Moran'
data['school_zone'][240]='Greenbrier'
data['school_zone'][246]='Greenbrier'
data['school_zone'][251]='Greenbrier'
data['school_zone'][253]='Greenbrier'
data['school_zone'][255]='Burnley-Moran'
data['school_zone'][256]='Burnley-Moran'
data['school_zone'][257]='Greenbrier'
data['school_zone'][258]='Split'
data['school_zone'][286]='Greenbrier'
data['school_zone'][288]='Split'
data['school_zone'][290]='Split'
data['school_zone'][304]='Greenbrier'
data['school_zone'][306]='Greenbrier'
data['school_zone'][311]='Greenbrier'
data['school_zone'][312]='Greenbrier'
data['school_zone'][313]='Burnley-Moran'
data['school_zone'][314]='Greenbrier'
data['school_zone'][315]='Greenbrier'
data['school_zone'][321]='Greenbrier'
data['school_zone'][344]='Split'
data['school_zone'][345]='Venable'
data['school_zone'][360]='Venable'
data['school_zone'][362]='Greenbrier'
data['school_zone'][366]='Greenbrier'
data['school_zone'][368]='Greenbrier'
data['school_zone'][369]='Venable'
data['school_zone'][371]='Greenbrier'
data['school_zone'][372]='Greenbrier'
data['school_zone'][373]='Venable'
data['school_zone'][377]='Venable'
data['school_zone'][380]='Venable'
data['school_zone'][384]='Venable'
data['school_zone'][385]='Venable'
data['school_zone'][386]='Venable'
data['school_zone'][390]='Burnley-Moran'
data['school_zone'][396]='Burnley-Moran'
data['school_zone'][398]='Burnley-Moran'
data['school_zone'][407]='Burnley-Moran'
data['school_zone'][408]='Burnley-Moran'
data['school_zone'][419]='Greenbrier'
data['school_zone'][421]='Greenbrier'
data['school_zone'][423]='Greenbrier'
data['school_zone'][425]='Greenbrier'
data['school_zone'][431]='Venable'
data['school_zone'][441]='Split'
data['school_zone'][450]='Split'
data['school_zone'][470]='Split'
data['school_zone'][472]='Split'
data['school_zone'][476]='Split'
data['school_zone'][477]='Greenbrier'
data['school_zone'][482]='Greenbrier'
data['school_zone'][484]='Greenbrier'
data['school_zone'][485]='Greenbrier'
data['school_zone'][486]='Greenbrier'
data['school_zone'][487]='Greenbrier'
data['school_zone'][488]='Greenbrier'
data['school_zone'][490]='Greenbrier'
data['school_zone'][493]='Greenbrier'
data['school_zone'][494]='Greenbrier'
data['school_zone'][495]='Greenbrier'
data['school_zone'][497]='Jackson-Via'
data['school_zone'][499]='Jackson-Via'
data['school_zone'][500]='Split'
data['school_zone'][501]='Split'
data['school_zone'][502]='Clark'
data['school_zone'][503]='Clark'
data['school_zone'][505]='Clark'
data['school_zone'][506]='Clark'
data['school_zone'][508]='Clark'
data['school_zone'][511]='Clark'
data['school_zone'][551]='Burnley-Moran'
data['school_zone'][552]='Clark'
data['school_zone'][553]='Clark'
data['school_zone'][554]='Clark'
data['school_zone'][557]='Clark'
data['school_zone'][569]='Clark'
data['school_zone'][571]='Burnley-Moran'
data['school_zone'][573]='Clark'
data['school_zone'][576]='Burnley-Moran'
data['school_zone'][618]='Burnley-Moran'
data['school_zone'][622]='Greenbrier'
data['school_zone'][623]='Greenbrier'
data['school_zone'][627]='Greenbrier'
data['school_zone'][633]='Burnley-Moran'
data['school_zone'][693]='Split'
data['school_zone'][707]='Split'
data['school_zone'][708]='Split'
data['school_zone'][709]='Venable'
data['school_zone'][710]='Burnley-Moran'
data['school_zone'][711]='Venable'
data['school_zone'][713]='Split'
data['school_zone'][715]='Split'
data['school_zone'][716]='Clark'
data['school_zone'][717]='Clark'
data['school_zone'][721]='Burnley-Moran'
data['school_zone'][722]='Burnley-Moran'
data['school_zone'][723]="Burnley-Moran"
data['school_zone'][740]="Clark"
data['school_zone'][742]='Burnley-Moran'
data['school_zone'][744]='Burnley-Moran'
data['school_zone'][745]='Clark'
data['school_zone'][748]='Burnley-Moran'
data['school_zone'][750]='Burnley-Moran'
data['school_zone'][751]='Burnley-Moran'
data['school_zone'][752]='Venable'
data['school_zone'][756]='Venable'
data['school_zone'][762]='Clark'
data['school_zone'][768]='Clark'
data['school_zone'][769]='Burnley-Moran'
data['school_zone'][779]='Johnson'
data['school_zone'][782]='Venable'
data['school_zone'][793]='Venable'
data['school_zone'][796]='Venable'
data['school_zone'][797]='Venable'
data['school_zone'][798]='Venable'
data['school_zone'][802]='Venable'
data['school_zone'][803]='Venable'

In [ ]:
data['school_zone'].value_counts()

In [ ]:
#The function inserted school names as tuples, so we need to standardize them
data['school_zone'] = data['school_zone'].apply(lambda x: x if type(x)==str else x[0])

In [ ]:
data['school_zone'].value_counts()

In [ ]:
#The splits are not very helpful, so we'll drop those
data = data[data['school_zone'] != 'Split']

In [ ]:
#Done with the shapes, so let's convert back to a standard dataframe
census = data.drop('geometry', axis=1)
census=pd.DataFrame(data)

In [ ]:
#Look at the available information
census.info()

In [ ]:
#Some of the information is irrelevant; some of it is the same for all rows; and some of it is repetitive.
#We will start with a selection of what seem like the most relevant features for our problem.
columns = ['BlockGroup', 'Population', 'White', 'Black', 'AmIndian', 'Asian', 'Hawaiian', 'Other', 
           'WhtBlk','Housing_Units', 'HU_Occupied', 'school_zone']
census = census[columns]

In [ ]:
#Import additional information from the Virginia Equity Project. Most of this data was initially collected by the 
#U.S. Census. This data is only recorded at the block group level, so it is less granular than the first data set.
blocks = pd.read_csv('data/regional_atlas_block_groups.csv')
blocks

In [ ]:
#This data is for the larger region, and we want to zoom in on just the city of Charlottesville
blocks['county.nice'].value_counts()

In [ ]:
#We will make a new dataframe of just the Charlottesville block groups.
blocks.rename(columns={"county.nice": "county"}, inplace=True)
cc_blocks = blocks[blocks.county=="Charlottesville City"]
cc_blocks.info()

In [ ]:
#Many columns are all nulls, and others repeat information we already have. Additionally there are features that 
#are not relevant to our question, like water acreage. We will keep the novel features that relate to demographics.
block_columns = ['GEOID', 'totalpopE', 'hhincE','hsmoreE', 'bamoreE', 'gradmoreE', 'unempE', 'hlthinsE', 'pubinsE', 
                 'allhseE','snapE', 'renter30E', 'homeownE', 'vacrateE', 'age17E', 
                 'age24E', 'age64E', 'age65E']
cc_blocks = cc_blocks[block_columns]
cc_blocks

In [ ]:
#Check our updated dataframe to see our data types and remaining nulls.
cc_blocks.info()

In [ ]:
#Necessary setup to merge the two dataframes.
census['BlockGroup'] = census['BlockGroup'].astype(int)
census = census.rename(columns={'BlockGroup':'GEOID'})

In [ ]:
#Merge the block data with the block group data, using "GEOID" as the key.
census = census.merge(cc_blocks, how='left', on='GEOID')
census

In [ ]:
census.info()

In [ ]:
#Population is not very meaningful as a number, since the different blocks are of disparate sizes. I engineered a
#feature to make the number more comparable across blocks. I did the same with SNAP benefits recipients, since this
#data was provided as a raw number.
census['Density'] = census['Population']/census['Housing_Units']
census['SNAP_rate'] = census['totalpopE']/census['snapE']
census.replace(float('inf'), 0, inplace=True)
census["Density"].fillna(0, inplace = True)

In [ ]:
#Drop our target (and a few other features we no longer need) to begin modeling
X = census.drop(['school_zone', 'GEOID', 'Population', 'Housing_Units', 'totalpopE', 'snapE'], axis=1)
y = census['school_zone']

In [ ]:
#Split our data so we have a holdout testing set later.
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.25, random_state=12)

## Modeling and Evaluation

I began with two dummy models. A model that randomly predicts one of the six elementary schools each time would be accurate 17.3% of the time. A model that always predicts the school that covers the most census blocks would be right 32.1% of the time.

In [ ]:
#Let's start with dummy models.

dummy= DummyClassifier(strategy='uniform')
random_guess = dummy.fit(X_train, y_train).score(X_test, y_test)

dummy2 = DummyClassifier(strategy='most_frequent')
guessing_venable = dummy2.fit(X_train, y_train).score(X_test, y_test)

random_guess, guessing_venable

After cleaning my data and running it through a process of principal component analysis (PCA) to address issues of multicollinearity, I tried both a logistic regression, a decision tree, and a random forest. After running a grid search to avoid overfitting, my random forest model performed the best, and it ultimately resulted in an accuracy score of 88.8% on testing data.

In [ ]:
#Our data will need to be scaled, and we do have two columns with some nulls. Knowing household income and 
#the percentage of burdened renters (paying more than 30% of income in rent) is useful to our question, so we 
#don't want to lose that data, so we will use a KNNImputer to fill in the few remaining null values. Our data 
#has the potential to be quite collinear, since so many markers of financial well-being correlate. Using PCA
#with our model can address this issue. The model initially struggled to converge so we set the maximum iterations 
#to a higher number.

pipe = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), ('pca', PCA()),
                       ('lr', LogisticRegressionCV(multi_class='multinomial', max_iter=10000))])


In [ ]:
#Our target variable is categorical so we encode those categories
le = LabelEncoder()
y_train_labelled = le.fit_transform(y_train)

In [ ]:
#PCA logistic regression
pipe.fit(X_train, y_train_labelled).score(X_train, y_train_labelled)

In [ ]:
#Decision tree with grid search
# tree_pipe = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
#                             ('tree', DecisionTreeClassifier(max_depth=6))])

# parameters={'tree__max_depth': [10, 12, 14, 16, 18], 'tree__min_samples_leaf': (1, 2, 3, 4)}
# tree_gs = GridSearchCV(tree_pipe, parameters)
# tree_gs.fit(X_train, y_train_labelled).score(X_train, y_train_labelled)

#Here I'll input the best parameters from that grid search so we don't have to keep running it
tree_grid_search = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
                            ('tree', DecisionTreeClassifier(max_depth=16, min_samples_leaf=2))])
tree_grid_search.fit(X_train, y_train_labelled).score(X_train, y_train_labelled)

In [ ]:
#Random Forest with grid search
# random_forest = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
#                             ('rf', RandomForestClassifier())])

# forest_params = {'rf__n_estimators': [30, 40, 50, 60], 
#                  'rf__max_depth': [12, 13, 14], 
#                  'rf__max_features': [4, 5, 6, 7, 8, 9]}
# rf_gs = GridSearchCV(random_forest, forest_params)
# rf_gs.fit(X_train, y_train_labelled).score(X_train, y_train_labelled)

#Random forest model with the best parameters from the grid search
rf_grid_search = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
                            ('rf', RandomForestClassifier(max_depth=14, max_features=5, n_estimators=40))])
rf_grid_search.fit(X_train, y_train_labelled).score(X_train, y_train_labelled)

In [ ]:
#Let's try a boost to make the trees in our forest a bit more responsive
# boosted = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), ('xgb', xgboost.XGBClassifier(
#                                 random_state=12))])

# boost_params = {'xgb__n_estimators': [25, 50, 75, 100, 125, 150], 
#                  'xgb__max_depth': [2, 4, 6, 8, 10, 12, 14, 16, 18, 20],
#                'xgb__learning_rate': [.001, .01, .1, 1]}
# boosted_gs = GridSearchCV(boosted, boost_params)
# boosted_gs.fit(X_train, y_train_labelled).score(X_train, y_train_labelled)
# boosted_gs.best_params_
print('''{'xgb__learning_rate': 0.01, 'xgb__max_depth': 6, 'xgb__n_estimators': 125}''')
#Boosted model with best parameters from grid search
boosted_grid_search = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
                                      ('xgb', xgboost.XGBClassifier(random_state=12, 
                                                                   n_estimators=125, max_depth=6, learning_rate=.01))])
boosted_grid_search.fit(X_train, y_train_labelled).score(X_train, y_train_labelled)

That didn't improve the model, so our best model is the random forest grid search model.

In [ ]:
#Investigate feature importances to determine which features are heavily weighted by the model
importances = rf_grid_search.named_steps["rf"].feature_importances_
features = rf_grid_search.feature_names_in_

In [ ]:
feature_importances = pd.DataFrame({'Feature': features, 'Importance': importances})

feature_importances = feature_importances.sort_values(by='Importance', ascending=False)

print(feature_importances)

The top ten feature importances for this model were all non-racial features, so it appears that demographics are very predictive of school zone, but race alone may not be. My next model tested this hypothesis.

I removed all features that were not describing the racial makeup of the block, ran a PCA, and tried the same three model types. Again, the decision tree with grid searched hyperparameters was the best model, but even it only predicted correctly 33.2% of the time on testing data. (Even in its wildly overfit training version it barely crossed 55%, nowhere close to the full demographics model)

In [ ]:
X.info()

In [ ]:
race_features = ['White', 'Black', 'AmIndian', 'Asian', 'Hawaiian', 'Other', 'WhtBlk']
race = X[race_features]
race_train, race_test, y_train, y_test = train_test_split(race, y, test_size=.25, random_state=12)

In [ ]:
#Logistic regression using only racial composition of the block

pipe_race = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), ('pca', PCA()),
                       ('lr', LogisticRegressionCV(multi_class='multinomial', max_iter=10000))])
pipe_race.fit(race_train, y_train_labelled)
pipe_race.score(race_train, y_train_labelled)

In [ ]:
#Decision tree using only racial composition of census block
# tree_race = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
#                             ('tree', DecisionTreeClassifier(max_depth=6))])

# parameters2={'tree__max_depth': [2, 3, 4, 5, 6], 'tree__min_samples_leaf': (1, 2, 3, 4)}

# tree_gs_race = GridSearchCV(tree_race, parameters2)
# tree_gs_race.fit(race_train, y_train_labelled).score(race_train, y_train_labelled)

#Model with best parameters from grid search

tree_grid_search_race = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
                            ('tree', DecisionTreeClassifier(max_depth=5, min_samples_leaf=4))])
tree_grid_search_race.fit(race_train, y_train_labelled).score(race_train, y_train_labelled)

In [ ]:
#Random forest using only racial composition of census block
# rf_race = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
#                             ('rf', RandomForestClassifier())])

# forest_params = {'rf__n_estimators': [20, 30, 40, 50, 60, 70, 80, 90, 100], 
#                  'rf__max_depth': [8, 9, 10, 11, 12, 13, 14, 15], 
#                  'rf__max_features': [1, 2, 3, 4]}
# rf_race_gs = GridSearchCV(rf_race, forest_params)
# rf_race_gs.fit(race_train, y_train_labelled).score(race_train, y_train_labelled)

#Running with best parameters in place
rf_race_grid_search = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
                            ('rf', RandomForestClassifier(max_depth=8, max_features=1, n_estimators=90))])
rf_race_grid_search.fit(race_train, y_train_labelled).score(race_train, y_train_labelled)

Our model with full demographic information is much stronger than our race-only model. Our random forest models were the best for both versions of our data set. It's time to see how they perform with unseen data.

In [ ]:
#Evaluate our best model of all data on the test set
rf_grid_search.score(X_test, y_test)

That's a high score. Demographic data can powerfully predict what school zone a block is in. Intuitively that makes sense, as neighborhoods are rarely heterogenous, especially with regards to income and related factors.

In [ ]:
#Evaluate our best model of just racial demographics on the test set
rf_race_grid_search.score(race_test, y_test)

Just using racial data yields a model barely better than random guessing. It appears the other demographic data may be more important in predicting school zone.

In [ ]:
#Get a sense of where the model is working well or struggling.
block_predictions = confusion_matrix(y_test, rf_grid_search.predict(X_test))
disp = ConfusionMatrixDisplay(block_predictions)
disp.plot();

The model does well, though it struggles particularly with identifying Burnley-Moran (label 4). Burnley-Moran was well represented in our training set, so the model's challenges with this school suggest that perhaps its component blocks are especially heterogeneous compared to the blocks in other school zones.

In [ ]:
#Check the same for the race-only model
block_predictions_race = confusion_matrix(y_test, rf_race_grid_search.predict(race_test))
disp2 = ConfusionMatrixDisplay(block_predictions_race)
disp2.plot();

The race only model seems to almost exclusively predict Clark or Venable Elementary. Our dummy model always picked Venable, so it's not surprising that the two models have similar scores.

Socioeconomic factors are often blamed in conversations about educational equity, so I was curious to see what happened if I constructed a similar model but with only the non-racial demographic data.  This last model will look at all of our demographic data besides racial composition. Most of this data came from the Virginia Equity Center and was only available at the block group level, so less granularity might have an impact on how well the model works. That model performed almost as well as overall model, accurately predicting school zone in 85.7% of the testing data. 

In [ ]:
other_demo = X.drop(race_features, axis=1)

In [ ]:
other_demo

In [ ]:
demo_train, demo_test, y_train, y_test = train_test_split(other_demo, y, test_size=.25, random_state=12)

# demo = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
#                             ('rf', RandomForestClassifier())])

# params = {'rf__n_estimators': [30, 40, 50, 60], 
#                  'rf__max_depth': [12, 13, 14], 
#                  'rf__max_features': [4, 5, 6, 7, 8, 9]}

# tree_gs_demo = GridSearchCV(demo, params)
# tree_gs_demo.fit(demo_train, y_train_labelled).score(demo_train, y_train_labelled)

#Model with grid searched parameters
tree_grid_search_demo = Pipeline(steps=[('knn', KNNImputer()), ('scale', StandardScaler()), 
                            ('rf', RandomForestClassifier(max_depth=14, max_features=6, n_estimators=40))])
tree_grid_search_demo.fit(demo_train, y_train_labelled).score(demo_train, y_train_labelled)

In [ ]:
tree_grid_search_demo.score(demo_test, y_test)

Just using non-race demographic information is almost as predictive as using all available features.

In [ ]:
#Prepare data for a map visualization
data['preds'] = rf_grid_search.predict(X)
data['race_preds'] = rf_race_grid_search.predict(race)

school_labels = {0:"Clark", 1: 'Jackson-Via', 2: 'Johnson', 3: 'Greenbrier', 4: 'Burnley-Moran', 5: 'Venable'}
data = data.replace({'preds': school_labels})
data = data.replace({'race_preds': school_labels})

In [ ]:
#Visualize the results. Clicking on any block shows the actual school zone and the zone predicted by both the full 
#and race-only models. The blocks that were close to evenly split between school zones are omitted and thus 
#have no color.

m2 = folium.Map(location=(38.034, -78.477), zoom_start=13)

folium.GeoJson(schools, style_function = lambda x: {"fillColor": 'red' if x['properties']['ZONE']=="Clark" 
else ('blue' if x['properties']['ZONE']=="Jackson-Via" 
else ('orange' if x['properties']['ZONE']=="Johnson" 
else ('yellow' if x['properties']['ZONE']=="Burnley-Moran"
else ('purple' if x['properties']['ZONE']=="Greenbrier" else 'green')))), "weight": 4, 
                                                                         "color": "black", 'fill_opacity':1, 
                                                                         'fill':True}).add_to(m2)

popup = GeoJsonPopup(
    fields=['school_zone', 'preds', 'race_preds'],
    aliases=["School Zone:", 'Predicted School Zone:', "Predicted School Zone, Racial Demographics Only:"],
    localize=True,
    labels=True,
    style="background-color: yellow;"
)
folium.GeoJson(data,
    style_function=lambda feature: {
        'weight':1,
        "color": "blue",
        'fill_opacity':0
    }, popup=popup
).add_to(m2)


m2

## Conclusion
This model does not serve an immediately practical purpose, and it was never intended to. If someone wants to know their school district, the city schools division offers an address lookup tool that is always right.

Instead, this model is intended to spark continued conversation. It appears that the school district has largely succeeded in drawing a map that is no longer explicitly racist. The map does still reflect a city dramatically divided by economic factors. These are not issues likely to be solved by redrawing the map, as they reflect the geography of housing in the city. If truly heterogenous schools were the ultimate goal, then students would have to travel all over town at random rather than attending their closest school. In addition to being a logistical nightmare, such a solution would surely be intolerable to the community.

The takeaway from this project is that the school map is no longer the place to direct our efforts towards increasing equity. School zoning was merely the first line of attack in efforts to tacitly keep schools segregated. While this project suggests that particular obstacle has been removed, the NYTimes article outlines many other areas of persistent discrimination, including access to advanced courses, gifted education, and a two-tiered diploma system. The public school system is no longer assigning students to schools in a directly racist way, but there's plenty of work still to be done.